In [2]:
import pandas as pd
import numpy as np

In [3]:
from fastparquet import ParquetFile
import s3fs
import boto3
from fastparquet.cencoding import from_buffer

In [3]:
conda install sqlitedict

Solving environment: unsuccessful initial attempt using frozen solve. Retrying with flexible solve.
Solving environment: unsuccessful initial attempt using frozen solve. Retrying with flexible solve.

PackagesNotFoundError: The following packages are not available from current channels:

  - sqlitedict

Current channels:

  - https://repo.anaconda.com/pkgs/main/linux-64
  - https://repo.anaconda.com/pkgs/main/noarch
  - https://repo.anaconda.com/pkgs/r/linux-64
  - https://repo.anaconda.com/pkgs/r/noarch

To search for alternate channels that may provide the conda package you're
looking for, navigate to

    https://anaconda.org

and use the search bar at the top of the page.



Note: you may need to restart the kernel to use updated packages.


In [4]:
from collections import defaultdict
from sqlitedict import SqliteDict
import zlib

In [5]:
# setting aws s3 client with boto3 explicitly

client = boto3.client(
    's3',
    region_name = 'sa-east-1'
)

# working with common crawl

In [41]:
# setting url's to common crawl s3 bucket and stablishing dataset
import pyarrow.dataset as ds

cc_index_s3_path = 's3://commoncrawl/cc-index/table/cc-main/warc/'
cc_index = ds.dataset(cc_index_s3_path, format='parquet', partitioning= 'hive')

In [7]:
# pulling data as fragments filtering by crawl date and web format
fragments = list(
    cc_index.get_fragments(
        filter=(ds.field('crawl')=="CC-MAIN-2022-05") &
        (ds.field('subset')=='warc')
    )
)

len(fragments)

300

In [8]:
%%time
# understanding dateset tho=rough statistics

fragments[0].row_groups[0].statistics

CPU times: user 8.3 ms, sys: 1.01 ms, total: 9.31 ms
Wall time: 2.63 s


{'url_surtkey': {'min': 'com,wordpress,freefall852)/2016/03/29/billy-guy',
  'max': 'com,worldpackers)/search/skill_hospitality_entertainment/type_hotel?location_categories[]=nature&location_types[]=hotel&min_meals_count[]=3&months[]=11&skills[]=music'},
 'url': {'min': 'http://03.worldchefsbible.com/',
  'max': 'https://zh.worldallianceofdramatherapy.com/he-mission'},
 'url_host_name': {'min': '03.worldchefsbible.com',
  'max': 'zr1.worldblast.com'},
 'url_host_tld': {'min': 'com', 'max': 'com'},
 'url_host_2nd_last_part': {'min': 'wordpress', 'max': 'worldpackers'},
 'url_host_3rd_last_part': {'min': '03', 'max': 'zr1'},
 'url_host_4th_last_part': {'min': 'bbbfoundation', 'max': 'www'},
 'url_host_5th_last_part': {'min': 'http', 'max': 'toolbox'},
 'url_host_registry_suffix': {'min': 'com', 'max': 'com'},
 'url_host_registered_domain': {'min': 'wordpress.com',
  'max': 'worldpackers.com'},
 'url_host_private_suffix': {'min': 'com', 'max': 'com'},
 'url_host_private_domain': {'min': '

In [9]:
%%time 

# stablishing file system to be used by parquet file
fs = s3fs.S3FileSystem()
pf = ParquetFile(fn = fragments[0].path, fs=fs)

CPU times: user 61.3 ms, sys: 14.1 ms, total: 75.5 ms
Wall time: 7.14 s


In [10]:
# setting functions to try to read fragments as parquet file

import time

def perform_s3_operation(fs):
    return  ParquetFile(fn = fragments[0].path, fs=fs)
    
def retry_with_exponential_backoff(fs, max_retries=5):
    retries = 0
    while retries < max_retries:
        try:
            pf = perform_s3_operation(fs)
            
            
        except Exception as e:
            print(f"Error: {e}")
            retries += 1
            wait_time = (2 ** retries)  # Exponential backoff
            print(f"Retrying in {wait_time} seconds...")
            time.sleep(wait_time)
    
    else:
        print("Max retries reached. Exiting.")
    return pf


In [11]:
# trying to read fragments as parquet file

pf = retry_with_exponential_backoff(fs)

# Verificar se pf é None antes de acessar seus atributos
if pf is not None:
    metadata = pf.fmd.row_groups[0].columns[0].meta_data._asdict()
    print(metadata)
else:
    print("ParquetFile object is None.")

Error: [Errno 16] Please reduce your request rate.
Retrying in 2 seconds...
{'type': 6, 'encodings': [0, 4], 'path_in_schema': ['url_surtkey'], 'codec': 2, 'num_values': 1730100, 'total_uncompressed_size': 117917394, 'total_compressed_size': 23113472, 'key_value_metadata': None, 'data_page_offset': 4, 'index_page_offset': None, 'dictionary_page_offset': None, 'statistics': {'max': None, 'min': None, 'null_count': 0, 'distinct_count': None, 'max_value': "b'com,worldpackers)/search/skill_hospitality_entertainment/type_hotel?location_categories[]=nature&location_types[]=hotel&min_meals_count[]=3&months[]=11&skills[]=music'", 'min_value': "b'com,wordpress,freefall852)/2016/03/29/billy-guy'"}, 'encoding_stats': [{'page_type': 0, 'encoding': 0, 'count': 122}], 'bloom_filter_offset': None}


In [25]:
#  showing metadata as dict
pf.fmd.row_groups[0].columns[0].meta_data._asdict()

{'type': 6,
 'encodings': [0, 4],
 'path_in_schema': ['url_surtkey'],
 'codec': 2,
 'num_values': 1730100,
 'total_uncompressed_size': 117917394,
 'total_compressed_size': 23113472,
 'key_value_metadata': None,
 'data_page_offset': 4,
 'index_page_offset': None,
 'dictionary_page_offset': None,
 'statistics': {'max': None,
  'min': None,
  'null_count': 0,
  'distinct_count': None,
  'max_value': "b'com,worldpackers)/search/skill_hospitality_entertainment/type_hotel?location_categories[]=nature&location_types[]=hotel&min_meals_count[]=3&months[]=11&skills[]=music'",
  'min_value': "b'com,wordpress,freefall852)/2016/03/29/billy-guy'"},
 'encoding_stats': [{'page_type': 0, 'encoding': 0, 'count': 122}],
 'bloom_filter_offset': None}

In [13]:
print(fragments[0].path)

commoncrawl/cc-index/table/cc-main/warc/crawl=CC-MAIN-2022-05/subset=warc/part-00000-1e2959d8-5649-433a-b76e-f1b876a6479d.c000.gz.parquet


In [ ]:
# trying to access fragments header to get some information without having to 
# show load the hole index or data

file = fragments[0].path
bucket, key =  file.split('/', 1)
metadata = client.head_object(Bucket= bucket, Key = key)
content_length = int(metadata['ContentLength'])
f'{content_length / (1024**3):0.1f} GB'

In [ ]:
# checking key
# maybe I'll have to check if the url structure I'm using right now still is compatible to 
# the way used to query data from the common cral bucket 

trial = fragments[0].path
bucket, key =  file.split('/', 1)
print(key)

In [ ]:

end_byte = content_length
start_byte = end_byte - 8

response = client.get_object(Bucket=bucket,
                         Key=key,
                         Range=f'bytes={start_byte}-{end_byte}')
end_content = response['Body'].read()

assert end_content[-4:] == b'PAR1'
file_meta_length = int.from_bytes(end_content[:4], byteorder='little')
f'{file_meta_length / 1024:0.1f} kb'

In [ ]:
import pyarrow.parquet as pq

s3_object_key = "cc_parquet_files_1"


In [ ]:
pq.write_to_dataset(table=cc_index.to_table(),
                   root_path = f's3://actum-dremio-test/{s3_object_key}',
                   filesystem=fs)

In [12]:
table = cc_index.to_table()
print(table)

NameError: name 'cc_index' is not defined

In [ ]:
cc_index.

# pulling  archives from bucket as random file

In [13]:
# algorith to get and upload data to actum-dremio-test without deleting previos registers. This 
# way duplicates are generated

bucket_name = 'actum-dremio-test'
prefixo_s3 = 'other/zip/1ac6c006-4c09-716a-1166-44117d404300/'
pyarrow_files = "pyarrow_files/"


resposta = client.list_objects(Bucket=bucket_name, Prefix=prefixo_s3)

for obj in resposta.get('Contents', []):
    chave_arquivo = obj['Key']
    
    if  "parquet" in chave_arquivo:
        print(f"Lendo arquivo: {chave_arquivo}")

        resposta = client.get_object(Bucket=bucket_name, Key=chave_arquivo)
        conteudo = resposta['Body'].read()

        pyarrow_file_c = os.path.join(pyarrow_files, os.path.basename(chave_arquivo))
        
        client.put_object(Body=conteudo, Bucket=bucket_name, Key=pyarrow_file_c)
        print(f'Successfully uploaded {chave_arquivo} to {pyarrow_files}')     


Lendo arquivo: other/zip/1ac6c006-4c09-716a-1166-44117d404300/1_0_0.parquet
Successfully uploaded other/zip/1ac6c006-4c09-716a-1166-44117d404300/1_0_0.parquet to pyarrow_files/


## pulling from base bucket, pushing to child folder, deleting

In [6]:
bucket_name = 'actum-dremio-test'
prefixo_s3 = ''
pyarrow_files = "pyarrow_files/"

In [7]:

import os

file_size = os.path.getsize("files/2.010669_iteration_14287.arrow")
print(file_size)

3130


In [ ]:
paginator = client.get_paginator('list_objects')
result_iterator = paginator.paginate(Bucket=bucket_name, Prefix=prefixo_s3)

for page in result_iterator:
    for obj in page.get('Contents', []):
        chave_arquivo = obj['Key']

        if "iteration" in chave_arquivo:
            print(f"Lendo arquivo: {chave_arquivo}")

            resposta = client.get_object(Bucket=bucket_name, Key=chave_arquivo)
            conteudo = resposta['Body'].read()

            pyarrow_file_c = os.path.join(pyarrow_files, os.path.basename(chave_arquivo))

            client.put_object(Body=conteudo, Bucket=bucket_name, Key=pyarrow_file_c)
            print(f'Successfully uploaded {chave_arquivo} to {pyarrow_files}')

            client.delete_object(Bucket=bucket_name, Key=chave_arquivo)
            print(f'Successfully deleted iteration {chave_arquivo} from base bucket: {bucket_name}')

Lendo arquivo: 19.299977_iteration_19584.arrow
Successfully uploaded 19.299977_iteration_19584.arrow to pyarrow_files/
Successfully deleted iteration 19.299977_iteration_19584.arrow from base bucket: actum-dremio-test
Lendo arquivo: 19.301102_iteration_51726.arrow
Successfully uploaded 19.301102_iteration_51726.arrow to pyarrow_files/
Successfully deleted iteration 19.301102_iteration_51726.arrow from base bucket: actum-dremio-test
Lendo arquivo: 19.305897_iteration_59258.arrow
Successfully uploaded 19.305897_iteration_59258.arrow to pyarrow_files/
Successfully deleted iteration 19.305897_iteration_59258.arrow from base bucket: actum-dremio-test
Lendo arquivo: 19.306611_iteration_43026.arrow
Successfully uploaded 19.306611_iteration_43026.arrow to pyarrow_files/
Successfully deleted iteration 19.306611_iteration_43026.arrow from base bucket: actum-dremio-test
Lendo arquivo: 19.311265_iteration_86104.arrow
Successfully uploaded 19.311265_iteration_86104.arrow to pyarrow_files/
Successfu

In [ ]:
from datetime import datetime

current_time = datetime.now()

print("terminou em:", current_time)

## reading archive as batch file (random)

In [43]:
import pyarrow as pa

In [81]:
with pa.RecordBatchFileReader(conteudo) as reader:
    table = reader.read_all()
    df = table.to_pandas()
df

timestamp                             sensor_id  temperature  \
0 2022-06-22 08:36:18  67efe674-8b2b-4cce-b83a-2b86ceb1de65        23.66   

   humidity  pressure  
0     42.17    912.58